In [1]:
!pip install git+https://github.com/openai/jukebox.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/openai/jukebox.git to /tmp/pip-req-build-6g3xit8x
  Running command git clone -q https://github.com/openai/jukebox.git /tmp/pip-req-build-6g3xit8x
     |████████████████████████████████| 60 kB 7.7 MB/s 
     |████████████████████████████████| 238 kB 51.2 MB/s 
     |████████████████████████████████| 3.5 MB 49.1 MB/s 
     |████████████████████████████████| 1.6 MB 31.4 MB/s 
     |████████████████████████████████| 2.5 MB 45.8 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 20.2 MB 1.2 MB/s 
     |████████████████████████████████| 3.1 MB 48.5 MB/s 
     |████████████████████████████████| 3.1 MB 45.2 MB/s 
     |████████████████████████████████| 3.1 MB 50.8 MB/s 
  Created wheel for jukebox: filename=jukebox-1.0-py3-none-any.whl size=197916 

IMPORTANT NOTE ON SYSTEM REQUIREMENTS:

If you are connecting to a hosted runtime, make sure it has a P100 GPU (optionally run !nvidia-smi to confirm). Go to Edit>Notebook Settings to set this.

CoLab may first assign you a lower memory machine if you are using a hosted runtime.  If so, the first time you try to load the 5B model, it will run out of memory, and then you'll be prompted to restart with more memory (then return to the top of this CoLab).  If you continue to have memory issues after this (or run into issues on your own home setup), switch to the 1B model.

If you are using a local GPU, we recommend V100 or P100 with 16GB GPU memory for best performance. For GPU’s with less memory, we recommend using the 1B model and a smaller batch size throughout.  



In [2]:
!nvidia-smi

Fri Nov 18 09:10:30 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   40C    P8     9W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [3]:
import jukebox
import torch as t
import librosa
import os
from IPython.display import Audio
from jukebox.make_models import make_vqvae, make_prior, MODELS, make_model
from jukebox.hparams import Hyperparams, setup_hparams
from jukebox.sample import sample_single_window, _sample, \
                           sample_partial_window, upsample
from jukebox.utils.dist_utils import setup_dist_from_mpi
from jukebox.utils.torch_utils import empty_cache
rank, local_rank, device = setup_dist_from_mpi()

Using cuda True


# Sample from the 5B or 1B Lyrics Model


In [4]:
model = "1b_lyrics"     
hps = Hyperparams()
hps.sr = 44100
hps.n_samples = 3 if model=='5b_lyrics' else 8
hps.name = 'samples'
chunk_size = 16 if model=="5b_lyrics" else 32
max_batch_size = 3 if model=="5b_lyrics" else 16
hps.levels = 3
hps.hop_fraction = [.5,.5,.125]

vqvae, *priors = MODELS[model]
vqvae = make_vqvae(setup_hparams(vqvae, dict(sample_length = 1048576)), device)
top_prior = make_prior(setup_hparams(priors[-1], dict()), vqvae, device)



Running  wget -O /root/.cache/jukebox/models/5b/vqvae.pth.tar https://openaipublic.azureedge.net/jukebox/models/5b/vqvae.pth.tar
Restored from /root/.cache/jukebox/models/5b/vqvae.pth.tar
0: Loading vqvae in eval mode
Creating cond. autoregress with prior bins [79, 2048], 
dims [384, 6144], 
shift [ 0 79]
input shape 6528
input bins 2127
Self copy is False
Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v3_artist_ids.txt
Loading artist IDs from /usr/local/lib/python3.7/dist-packages/jukebox/data/ids/v3_genre_ids.txt
Level:2, Cond downsample:None, Raw to tokens:128, Sample length:786432
Running  wget -O /root/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar https://openaipublic.azureedge.net/jukebox/models/1b_lyrics/prior_level_2.pth.tar
Restored from /root/.cache/jukebox/models/1b_lyrics/prior_level_2.pth.tar
0: Loading prior in eval mode


Specify your choice of artist, genre, lyrics, and length of musical sample. 

In [5]:
sample_length_in_seconds = 60          # Full length of musical sample to generate - we find songs in the 1 to 4 minute
                                       # range work well, with generation time proportional to sample length.  
                                       # This total length affects how quickly the model 
                                       # progresses through lyrics (model also generates differently
                                       # depending on if it thinks it's in the beginning, middle, or end of sample)

hps.sample_length = (int(sample_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
assert hps.sample_length >= top_prior.n_ctx*top_prior.raw_to_tokens, f'Please choose a larger sampling rate'

In [6]:
metas = [dict(artist = "Metallica",
            genre = "Rock",
            total_length = hps.sample_length,
            offset = 0,
            lyrics = """Say your prayers, little one
            Don't forget, my son
            To include everyone
            Tuck you in, warm within
            Keep you free from sin
            'Til the sandman, he comes
            Sleep with one eye open
            Gripping your pillow tight
            Exit light
            Enter night
            Take my hand
            We're off to never-never land
            Somethings wrong, shut the light
            Heavy thoughts tonight
            And they aren't of Snow White
            Dreams of war, dreams of liars
            Dreams of dragon's fire
            And of things that will bite, yeah
            """,
            ),
          ] * hps.n_samples
labels = [None, None, top_prior.labeller.get_batch_labels(metas, 'cuda')]

Optionally adjust the sampling temperature (we've found .98 or .99 to be our favorite).  


In [7]:
sampling_temperature = .98

lower_batch_size = 16
max_batch_size = 3 if model == "5b_lyrics" else 16
lower_level_chunk_size = 32
chunk_size = 16 if model == "5b_lyrics" else 32
sampling_kwargs = [dict(temp=.99, fp16=True, max_batch_size=lower_batch_size,
                        chunk_size=lower_level_chunk_size),
                    dict(temp=0.99, fp16=True, max_batch_size=lower_batch_size,
                         chunk_size=lower_level_chunk_size),
                    dict(temp=sampling_temperature, fp16=True, 
                         max_batch_size=max_batch_size, chunk_size=chunk_size)]

Now we're ready to sample from the model. We'll generate the top level (2) first, followed by the first upsampling (level 1), and the second upsampling (0).  In this CoLab we load the top prior separately from the upsamplers, because of memory concerns on the hosted runtimes. If you are using a local machine, you can also load all models directly with make_models, and then use sample.py's ancestral_sampling to put this all in one step.

After each level, we decode to raw audio and save the audio files.   

This next cell will take a while (approximately 10 minutes per 20 seconds of music sample)

In [8]:
zs = [t.zeros(hps.n_samples,0,dtype=t.long, device='cuda') for _ in range(len(priors))]
zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)

Sampling level 2
Sampling 6144 tokens for [0,6144]. Conditioning on 0 tokens
Ancestral sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
12/12 [00:05<00:00,  2.32it/s]
6144/6144 [08:15<00:00, 12.39it/s]
Sampling 6144 tokens for [768,6912]. Conditioning on 5376 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
180/180 [00:28<00:00,  6.40it/s]
768/768 [01:09<00:00, 11.03it/s]
Sampling 6144 tokens for [1536,7680]. Conditioning on 5376 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
180/180 [00:28<00:00,  6.42it/s]
768/768 [01:11<00:00, 10.80it/s]
Sampling 6144 tokens for [2304,8448]. Conditioning on 5376 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
180/180 [00:28<00:00,  6.42it/s]
768/768 [01:09<00:00, 11.03it/s]
Sampling 6144 tokens for [3072,9216]. Conditioning on 5376 tokens
Primed sampling 8 samples with temp=0.98, top_k=0, top_p=0.0
180/180 [00:28<00:00,  6.42it/s]
768/768 [01:10<00:00, 10.94it/s]
Sampling 6144 tokens f

Listen to the results from the top level (note this will sound very noisy until we do the upsampling stage).  You may have more generated samples, depending on the batch size you requested.

In [9]:
Audio(f'{hps.name}/level_2/item_0.wav')